In [1]:
import json
import pandas as pd
import folium
import geocoder
import shapefile
import io

In [7]:
# Create geojson file from shapefile
# raw = pd.read_excel('Home.xlsx')
# df = raw.set_index(['No'])

shp_path = "C:\\Users\\tiwang\\OneDrive - King County\\Desktop\\CC\\SODO\\workspace\\zipcodeSODO.shp"
# shp_path = "/Users/apple/Desktop/workspace/workspace/sodo.shp"


In [8]:
# create json file form shapefile for zipcode mapping
reader = shapefile.Reader(shp_path)
fields = reader.fields[1:]
field_names = [field[0] for field in fields]
buffer = []
for sr in reader.shapeRecords():
    atr = dict(zip(field_names, sr.record))
    geom = sr.shape.__geo_interface__
    buffer.append(dict(type="Feature", geometry=geom, properties=atr)) 

from json import dumps
geojson = open("sodo3.json", "w")
geojson.write(dumps({"type": "FeatureCollection","features": buffer}, indent=2) + "\n")
geojson.close()

In [3]:
# read in count data

sodo_geo = r"sodo3.json"
sodo_home = r'zipcode_0731.csv'
sodo_data = pd.read_csv(sodo_home)
# sodo_data


In [4]:
# choropleth map, distribution of respondents based on zipcode
m = folium.Map(location=[47.6144, -122.323], zoom_start=10,tiles='Mapbox Bright')
m.choropleth(geo_path=sodo_geo,data=sodo_data, columns=['zipcode', 'count'],
             key_on='feature.properties.GEOID10',fill_opacity=0.6, 
             threshold_scale=[1,5,10,15,20,25],fill_color='YlGn', line_opacity=0.6,
             line_color= "White",line_weight=1, legend_name='')
folium.TileLayer('cartodbpositron').add_to(m)
m.save("SoDo.html")
m



In [2]:
# clickable points with info of employer - part II

employer = r'valid_map.xlsx'
e_data = pd.read_excel(employer)

m = folium.Map(location=[47.591435, -122.332238], zoom_start=13,tiles='Mapbox Bright')

# after top 60, <= 1
c1 = '#006837'

# after top 20, <= 4
c2 = '#31a354'

# top 10 - 20, 5 - 14
c3 = '#78c679'

# top 6 - 10,  19 - 27
c4 = '#c2e699'

# top 5, 30 - 42
c5 = '#E6FF7B'


for index,item in e_data.iterrows():
    if item['count'] >= 30 :
        cc = c5
    elif item['count'] <= 27 and item['count'] >= 19 :
        cc = c4
    elif item['count'] <= 14 and item['count'] >= 7 :
        cc = c3
    elif item['count'] <= 6 and item['count'] > 1 :
        cc = c2
    elif item['count'] <=  1 :
        cc = c1
        
    text = str(item['employer'])+" ("+ str(item['real']) + ")"
    folium.CircleMarker(location=[item['lat'], item['lon']], radius=item['count']+2,
                    popup= text, color= "white", weight=0.2,
                    fill_color = cc, fill_opacity=0.4).add_to(m)
folium.TileLayer('cartodbpositron').add_to(m)
m.save("Employer.html")
m



In [114]:
# This is to get valid address (lat, lon) of employers for mapping - part I
emp = r'employer_0731.xlsx'
em = pd.read_excel(emp)
em = em[:]
invalid = []
valid = []

count = 0
for index, row in em.iterrows():
    count += 1
    if len(row['Address']) == 1:
        addr = row['Responses'] + " seattle address" 
        g = geocoder.google(addr)   
        print "json: " + g.json['address']
        address = g.json['address']
    else:
        address = row['Address']
        g = geocoder.google(address)
        print "manual: " + address
    d = {'employer':row['Responses'],'address':address, 'count':row['count'],'lat':g.json['lat'], 
             'lon':g.json['lng'],'zipcode':g.json['postal']}     
    valid.append(d)
    print count
    



manual: 2401 Utah Ave S, Seattle
1
manual: 2445 3rd Ave. S, Seattle
2
manual: 401 5th Ave, Seattle
3
manual: 4735 E Marginal Way S, Seattle
4
manual: not available
5
json: 1741 1st Avenue South, Seattle, WA 98134, USA
6
json: 2245 1st Avenue South, Seattle, WA 98134, USA
7
manual: 2711 Alaskan Way, Seattle
8
json: 1501 1st Avenue South, Seattle, WA 98134, USA
9
manual: 600 4th Avenue
10
json: 4100 4th Ave S, Seattle, WA 98134, USA
11
json: 1201 1st Avenue South #310, Seattle, WA 98134, USA
12
json: 1501 1st Avenue South #400, Seattle, WA 98134, USA
13
json: 66 S Hanford St #300, Seattle, WA 98134, USA
14
manual: not available
15
json: 5005 3rd Ave S, Seattle, WA 98134, USA
16
json: 1728 4th Ave S, Seattle, WA 98134, USA
17
json: 1250 1st Avenue South, Seattle, WA 98134, USA
18
manual:  1521 1st Ave S, Ste 500, Seattle, WA 98134
19
json: 5601 6th Ave S #300, Seattle, WA 98108, USA
20
json: 2124 4th Ave, Seattle, WA 98121, USA
21
json: 1400 S Lane St, Seattle, WA 98144, USA
22
json: 1501

In [36]:
# not used
# create json file 
g = geocoder.google(', Seattle')
# g.json

with open('data.txt', 'w') as outfile:
     json.dump(g.json, outfile, sort_keys = True, indent = 4,ensure_ascii = False)

In [ ]:
# folium map
# https://github.com/python-visualization/folium

# file options
# https://deparkes.co.uk/2016/06/10/folium-map-tiles/

# Color Brewer
# http://colorbrewer2.org/#type=sequential&scheme=BuGn&n=3